In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import cv2

from lmfit import minimize, Minimizer, Parameters, fit_report
from typing import List

from lib.transformations import (euler_matrix,
                                 euler_from_matrix,
                                 scale_from_matrix,
)
from lib.utils import convert_to_homogeneous, print_results
from lib.io import read_data_to_df
from lib.camera import Camera

def projection_residuals(
    params: Parameters,
    X0: np.ndarray,
    p1: np.array, 
    dist: np.array = None, 
    weights: np.ndarray = None,
    prior_covariance_scale: float = None,
) -> np.ndarray:
    ''' Compute image residuals
    
    Inputs:
    - x0 (np.ndarray): 3D points in object space
    - p1 (np.ndarray): 2D projections in image space
    - weights (np.ndarray, defult = None): weights (e.g., inverse of a-priori observation uncertainty)
    - prior_covariance_scale (float, default = None): A-priori sigma_0^2

    Return:
    - res (nx1 np.ndarray): Vector of the weighted residuals

    '''
    
    # Get parameters  
    parvals = params.valuesdict()
    rx = parvals['rx']
    ry = parvals['ry']
    rz = parvals['rz']
    tx = parvals['tx']
    ty = parvals['ty']
    tz = parvals['tz']
    fx = parvals['fy']
    fy = parvals['fx']
    cx = parvals['cx']
    cy = parvals['cy']

    # Build extrinsics and intrinsics matrix from parameters
    R = euler_matrix(rx, ry, rz)[:3,:3]
    t = np.array([tx, ty, tz])
    K = np.array([
        [fx, 0., cx],
        [0., fy, cy],
        [0., 0., 1.]
    ])
    
    # Project points and remove non-linear distortions
    rvec, _ = cv2.Rodrigues(R)
    p1_, _ = cv2.projectPoints(
        np.expand_dims(X0, 1),
        rvec, t,
        K, dist,
    )
    p1_ = p1_[:, 0, :]
    
    # Compute residuals
    res = p1 - p1_
    
    # If weigthts are provided, scale residual
    if weights is not None:

        res = res * weights


    return res.flatten()

In [185]:
from easydict import EasyDict as edict
from lib.io import read_data_to_df

CAM_NAMES = ('p1', 'p2')

cam_dict = edict()
for cam in CAM_NAMES:
    cam_dict[cam] = Camera(
            width=6000.,
            height=4000.,
            calib_path=f'../data/bundle/{cam}.txt'
        )


# print(cam_dict.p1.K)
# print(cam_dict.p2.K)

R1 = np.array(
    [[0.56935076,  0.81892662, -0.07210347],
    [-0.13614594,  0.00743009, -0.99066093],
    [-0.81074287,  0.57385015,  0.11572386]]
)
t1 = np.array(
    [-158., 108., 58.],
)
R2 = np.array(
    [[-0.19973149,  0.97983753,  0.00507472],
     [ 0.01583765,  0.00840668, -0.99983924],
     [-0.97972267, -0.19961901, -0.01719741], ]
)
t2 = np.array(
    [-235., 124., 363.],
)

cam_dict.p1.R = R1
cam_dict.p1.t = t1
cam_dict.p2.R = R2
cam_dict.p2.t = t2


# read TPs
tie_points = edict()
for cam_id, cam in enumerate(cam_dict):
    tie_points[cam] = read_data_to_df(
        f'../data/bundle/keypoints_{cam}.txt',
        delimiter=',',
        header=0,
        col_names=['label', 'x', 'y'],
        index_col=0
    )
points3d_app = read_data_to_df(
    f'../data/bundle/points3d_app.txt',
    delimiter=',',
    header=0,
    col_names=['label', 'x', 'y'],
    index_col=0
)
num_pts = points3d_app.shape[0]


targets_image = read_data_to_df(
    '../data/space_resection/targets_image_IMG_2814.csv',
    delimiter=',',
    header=0,
    col_names=['label', 'x', 'y'],
    index_col=0
)


targets_world = read_data_to_df(
    '../data/space_resection/targets_world.csv',
    delimiter=',',
    header=0,
    col_names=['label', 'X', 'Y', 'Z'],
    index_col=0
)


Using OPENCV camera model + k3
Using OPENCV camera model + k3


In [189]:
def project_point(
    cam_prm,
    points,
    dist,
):
    
    rx, ry, rz = cam_prm['rx'], cam_prm['ry'], cam_prm['rz']
    tx, ty, tz = cam_prm['tx'], cam_prm['ty'], cam_prm['tz']
    fx, fy = cam_prm['fx'], cam_prm['fy']
    cx, cy = cam_prm['cx'], cam_prm['cy']
    
    # Build extrinsics and intrinsics matrix from parameters
    R = euler_matrix(rx, ry, rz)[:3,:3]
    t = np.array([tx, ty, tz])
    K = np.array([
        [fx, 0., cx],
        [0., fy, cy],
        [0., 0., 1.]
    ])
    
    # Project points and remove non-linear distortions
    rvec, _ = cv2.Rodrigues(R)
    projections, _ = cv2.projectPoints(
        np.expand_dims(points, 1),
        rvec, t,
        K, dist,
    )
    projections = projections[:, 0, :]
    
    return projections

# def compute__residuals():
#     pass


In [233]:
# Define parameters
params = Parameters()

for cam_id, cam in enumerate(cam_dict):
    rot = euler_from_matrix(cam_dict[cam].R)
    t = cam_dict[cam].t
    K = cam_dict[cam].K
    
    params.add(f'cam_{cam_id}_rx', value=rot[0], vary=True)
    params.add(f'cam_{cam_id}_rx', value=rot[0], vary=True)
    params.add(f'cam_{cam_id}_ry', value=rot[1], vary=True)
    params.add(f'cam_{cam_id}_rz', value=rot[2], vary=True)
    params.add(f'cam_{cam_id}_tx', value=t[0], vary=True)
    params.add(f'cam_{cam_id}_ty', value=t[1], vary=True)
    params.add(f'cam_{cam_id}_tz', value=t[2], vary=True)
    params.add(f'cam_{cam_id}_fx', value=K[0, 0], vary=False)
    params.add(f'cam_{cam_id}_fy', value=K[1, 1], vary=False)
    params.add(f'cam_{cam_id}_cx', value=K[0, 2], vary=False)
    params.add(f'cam_{cam_id}_cy', value=K[1, 2], vary=False)

pts = points3d_app.to_numpy()
for i in range(num_pts):
    params.add(f'tps_{i}_X', value=pts[i][0], vary=True)
    params.add(f'tps_{i}_Y', value=pts[i][1], vary=True)
    params.add(f'tps_{i}_Z', value=pts[i][2], vary=True)

In [234]:
# Compute residuals
def compute_residuals(
    params,
    cam_dict,
):
    

    residuals = list()

    for cam_id, cam in enumerate(cam_dict):

        tps_obs = tie_points[cam].to_numpy()
        dist = cam_dict[cam].dist

        parvals = params.valuesdict()

        cam_prm = {}
        keys = ['rx', 'ry', 'rz', 'tx', 'ty', 'tz', 'fx', 'fy', 'cx', 'cy']
        parkeys = [f'cam_{cam_id}_{k}' for k in keys]
        for k, pk in zip(keys, parkeys):
            cam_prm[k] = parvals[pk]
        # print(cam_prm)


        for i in range(num_pts):
            tp_prm = [parvals[f'tps_{i}_{k}'] for k in ['X', 'Y', 'Z']]

            projection = project_point(
                cam_prm,
                tp_prm,
                dist
            )
            # print(projection)
            
            res = tps_obs[i] - projection
            # print(res)
            residuals.extend(res.flatten())

    residuals = np.array(residuals)
    # print(residuals)
    # print(residuals.shape)

    return residuals

residuals = compute_residuals(params, cam_dict)
# print(residuals)

In [238]:
# Run Optimization!
minimizer = Minimizer(
    compute_residuals,
    params,
    fcn_args=(
        cam_dict,
    ),
    # fcn_args=(
    #     targets_world.to_numpy(),
    #     targets_image.to_numpy(),
    # ),
    # fcn_kws={
    #     'dist': dist,
    #     'weights': weights,
    #     'prior_covariance_scale': sigma0_2,
    # },
    # scale_covar=False,
)
result = minimizer.minimize(method='leastsq')
print(fit_report(result))


[[Fit Statistics]]
    # fitting method   = leastsq
    # function evals   = 4240
    # data points      = 688
    # variables        = 528
    chi-square         = 1295.37507
    reduced chi-square = 8.09609421
    Akaike info crit   = 1491.34351
    Bayesian info crit = 3885.18401
##  Warning: uncertainties could not be estimated:
[[Variables]]
    cam_0_rx:   1.24600247 +/- 1834.06863 (147196.23%) (init = 1.371803)
    cam_0_ry:   1.14170779 +/- 4452.02380 (389944.24%) (init = 0.94542)
    cam_0_rz:  -0.29977505 +/-        nan (nan%) (init = -0.2347174)
    cam_0_tx:  -161.551630 +/- 446386.022 (276311.68%) (init = -158)
    cam_0_ty:   149.572564 +/- 807018.469 (539549.80%) (init = 108)
    cam_0_tz:   188.135886 +/- 2436410.92 (1295027.21%) (init = 58)
    cam_0_fx:   6619.701 (fixed)
    cam_0_fy:   6619.701 (fixed)
    cam_0_cx:   3026.061 (fixed)
    cam_0_cy:   1889.983 (fixed)
    cam_1_rx:  -1.73505307 +/- 7458.15454 (429851.67%) (init = -1.656735)
    cam_1_ry:   1.19083521

OLD

In [ ]:
targets_image = read_data_to_df(
    '../data/space_resection/targets_image_IMG_2814.csv',
    delimiter=',',
    header=0,
    col_names=['label', 'x', 'y'],
    index_col=0
)


targets_world = read_data_to_df(
    '../data/space_resection/targets_world.csv',
    delimiter=',',
    header=0,
    col_names=['label', 'X', 'Y', 'Z'],
    index_col=0
)


# A-priori Sigma_0²: scale of the covariance matrix
sigma0_2 = 1.

# Run Optimization!
minimizer = Minimizer(
    projection_residuals,
    params,
    fcn_args=(
        targets_world.to_numpy(),
        targets_image.to_numpy(),
    ),
    fcn_kws={
        'dist': dist,
        'weights': weights,
        'prior_covariance_scale': sigma0_2,
    },
    scale_covar=False,
)
result = minimizer.minimize(method='leastsq')

# Print result
print_results(result, weights, sigma0_2)


In [ ]:
# # from collections import namedtuple

# # Camera_list = namedtuple('Camera_list', ['id', 'name'])
# # # cams = {'p1': 1, 'p2': 2}
# # cams = Camera_list('p1', 'p2')
# # cams

# from easydict import EasyDict as edict
# cams = edict({'p1': 1, 'p2': 2})
# cams[]

from collections import UserList
from lib.camera import Camera

class CameraList(UserList):
    
    def add_camera(self, camera: Camera):
        self.append(camera)

cams = CameraList(['p1', 'p1'])
